In [24]:
import sys
    
import numpy as np

import os

try:
    import plotly.graph_objects as go
    from plotly.subplots import make_subplots
    import plotly.io as pio
    from plotly.offline import iplot, init_notebook_mode

except ModuleNotFoundError or ImportError:
    !{sys.executable} -m pip install plotly
    
    import plotly.graph_objects as go
    from plotly.subplots import make_subplots
    import plotly.io as pio
    from plotly.offline import iplot, init_notebook_mode

pio.renderers.default = 'notebook'
pio.templates.default = "seaborn"

try:
    import nPDyn
    from nPDyn.models.Model import Model
    from nPDyn.models.Presets import (lorentzian, gaussian, delta, conv_delta, 
                                      conv_lorentzian_gaussian, conv_lorentzian_lorentzian)
except ModuleNotFoundError or ImportError:
    !{sys.executable} -m pip install git+https://github.com/kpounot/nPDyn@dev#egg=nPDyn

    import nPDyn
    from nPDyn.models.Model import Model
    from nPDyn.models.Presets import (lorentzian, gaussian, delta, conv_delta, 
                                      conv_lorentzian_gaussian, conv_lorentzian_lorentzian)


## Instanciating a model, here a pseudo-Voigt profile

In [36]:
X = np.arange(-30, 30, 0.01)

params = {'scale': 1, 'a':0.8, 'gauWidth':0.3, 'lorWidth':0.25, 'shift': 0.0, 'bkgd':0.001}

m = Model(params=params, xVar=X)

m.eisfComponents['Lorentzian'] = (lorentzian, lambda p: [p['scale'] * (1 - p['a']), p['lorWidth'], p['shift']])
m.eisfComponents['Gaussian'] = (gaussian, lambda p: [p['scale'] * p['a'], p['gauWidth'], p['shift']])
m.bkgdComponents['bkgd'] = (lambda x, bkgd: np.zeros_like(x) + bkgd, lambda p: [p['bkgd']])

m.getModel()


array([0.00101768, 0.00101769, 0.00101771, ..., 0.00101772, 0.00101771,
       0.00101769])

## Plotting the model with default or given parameters

In [37]:
fig = go.FigureWidget(layout=go.Layout(xaxis=dict(title='$\\rm \hbar\omega~ [\mu eV]$'),
                                 yaxis=dict(title='$\\rm S(q,\omega)$', type='log')))

fig.add_trace(go.Scatter(x=X, y=m.getModel(), name='a=0.8'))
fig.add_trace(go.Scatter(x=X, y=m.getModel(params={'a': 0.5}), name='a=0.5'))

fig.show()

## Plotting components along with the model

In [4]:
names, eisf = m.getComponents(compType='eisf')

fig = go.FigureWidget(layout=go.Layout(xaxis=dict(title='$\\rm \hbar\omega~ [\mu eV]$', range=[-30, 30]),
                                 yaxis=dict(title='$\\rm S(q,\omega)$', type='log', range=[-4, 0.5])))

for line, label in zip(eisf, names):
    fig.add_trace(go.Scatter(x=X, y=line, name=label, line=dict(dash="dash")))
    
fig.add_trace(go.Scatter(x=X, y=m.getComponents(compType='bkgd')[1][0], name='bkgd', line=dict(dash='dot')))

fig.add_trace(go.Scatter(x=X, y=m.getModel(), name='Model'))
    
fig.show()

## Performing a convolution

In [10]:
p2 = {'scale': 10, 'pos': -2, 'bkgd': 0.001}

m2 = Model(params=p2, xVar=X)

m2.eisfComponents['Delta'] = (delta, lambda p: [p['scale'], p['pos']], 
                              {'gaussian': conv_delta, 'lorentzian': conv_delta})
m2.bkgdComponents['bkgd'] = (lambda x, bkgd: np.zeros_like(x) + bkgd, lambda p: [p['bkgd']])

m2.getModel(convolve=m)

fig = go.FigureWidget(layout=go.Layout(xaxis=dict(title='$\\rm \hbar\omega~ [\mu eV]$'),
                                 yaxis=dict(title='$\\rm S(q,\omega)$', type='log')))

fig.add_trace(go.Scatter(x=X, y=m.getModel(), name='resolution'))
fig.add_trace(go.Scatter(x=X, y=m2.getModel(convolve=m), name='convolution'))

fig.show()

## Using q-dependent parameters for linewidth

In [40]:
params = {'a': 0.5, '$\Gamma_1$': 7, '$\Gamma_2$': 32, 'bkgd': 0.0005, 'MSD': 2, 'shift': 0.0}

m3 = Model(params=params, xVar=X[np.newaxis, :])

qVals = np.arange(0.2, 2, 0.2)[:, np.newaxis]

m3.qisfComponents['Global'] = (lorentzian, lambda p: [p['a'] * np.exp(-qVals**2 * p['MSD']),
                                                      p['$\Gamma_1$'] * qVals**2,
                                                      p['shift']],
                               {'lorentzian': conv_lorentzian_lorentzian,
                                'gaussian': conv_lorentzian_gaussian})

m3.qisfComponents['Internal'] = (lorentzian, lambda p: [(1 - p['a']) * np.exp(-qVals**2*p['MSD']),
                                                        p['$\Gamma_2$'] * qVals**2,
                                                        p['shift']],
                                 {'lorentzian': conv_lorentzian_lorentzian,
                                  'gaussian': conv_lorentzian_gaussian})

m3.bkgdComponents['bkgd'] = (lambda x, bkgd: np.zeros_like(x) + bkgd,
                             lambda p: [p['bkgd']])

fig = go.FigureWidget(layout=go.Layout(xaxis=dict(title='$\\rm \hbar\omega~ [\mu eV]$', range=[-30, 30]),
                                       yaxis=dict(title='$\\rm S(q,\omega)$', type='log', range=[-4, 0.1])))


model = m3.getModel()

for idx, line in enumerate(model):
    fig.add_trace(go.Scatter(x=m3.xVar[0], y=m3.getModel()[idx], 
                             name='$\\rm q=%.1f ~ [\mathring{A}^{-1}]$' % qVals[idx]))
    
fig.show()
